In [1]:
import pandas as pd 
import seaborn as sns 
import matplotlib as plt 
%matplotlib inline
import glob
import csv
import tarfile
from tqdm import tqdm
import json

In [2]:
files = glob.glob('../BL_Work/openPrescribe/serialized/*.gz')
print files

['../BL_Work/openPrescribe/serialized/201009.gz', '../BL_Work/openPrescribe/serialized/201008.gz', '../BL_Work/openPrescribe/serialized/201011.gz', '../BL_Work/openPrescribe/serialized/201010.gz', '../BL_Work/openPrescribe/serialized/201012.gz']


In [3]:
import logging
logger = logging.getLogger()
fhandler = logging.FileHandler(filename='Computation_Marginals.log', mode='a')
formatter = logging.Formatter('%(asctime)s - %(name)s - %(levelname)s - %(message)s')
fhandler.setFormatter(formatter)
logger.addHandler(fhandler)
logger.setLevel(logging.DEBUG)

In [4]:
pdp = pd.read_csv(files[0],compression='gzip')
pdp.head(n=1000)

Unnamed: 0    0    1       2                3  \
0             0  Q30  5D7  A86001  0501013B0AAAJAJ   
1             1  Q30  5D7  A86003  0101010G0AAABAB   
2             2  Q30  5D7  A86003  0101010G0BBABAB   
3             3  Q30  5D7  A86003  0101010G0BCABAB   
4             4  Q30  5D7  A86003  0101010L0BBABAA   
5             5  Q30  5D7  A86003  0101010R0AAABAB   
6             6  Q30  5D7  A86003  0101010R0BCAAAB   
7             7  Q30  5D7  A86003  0101021B0AAAHAH   
8             8  Q30  5D7  A86003  0101021B0AAAJAJ   
9             9  Q30  5D7  A86003  0101021B0AAAPAP   
10           10  Q30  5D7  A86003  0101021B0AAAQAQ   
11           11  Q30  5D7  A86003  0101021B0BEADAJ   
12           12  Q30  5D7  A86003  0101021B0BEAIAL   
13           13  Q30  5D7  A86003  0101021B0BEAKAQ   
14           14  Q30  5D7  A86003  0101021B0BEAQAP   
15           15  Q30  5D7  A86003  0101021B0BFAAAF   
16           16  Q30  5D7  A86003  0101021B0BIAAAH   
17           17  Q30  5D7  A86003  0102000J0AAABAB   
18           18  Q30  5D7  A86003  0102000J0AAACAC   
19           19  Q30  5D7  A86003  0102000L0AAADAD   
20           20  Q30  5D7  A86003  0102000N0AAABAB   
21           21  Q30  5D7  A86003  0102000N0BBAAAB   
22           22  Q30  5D7  A86003  0102000P0AAABAB   
23           23  Q30  5D7  A86003  0102000P0AAADAD   
24           24  Q30  5D7  A86003  0102000P0BCABAB   
25           25  Q30  5D7  A86003  0102000T0AAAAAA   
26           26  Q30  5D7  A86003  0102000X0AAAAAA   
27           27  Q30  5D7  A86003  0102000Y0AAAFAF   
28           28  Q30  5D7  A86003  0103010D0AAAAAA   
29           29  Q30  5D7  A86003  0103010D0AAABAB   
..          ...  ...  ...     ...              ...   
970         970  Q30  5D7  A86003  0501050A0AAABAB   
971         971  Q30  5D7  A86003  0501050B0AAAAAA   
972         972  Q30  5D7  A86003  0501050B0AAADAD   
973         973  Q30  5D7  A86003  0501050C0AAABAB   
974         974  Q30  5D7  A86003  0501050C0AAAKAK   
975         975  Q30  5D7  A86003  0501050H0AAAAAA   
976         976  Q30  5D7  A86003  0501050H0AAABAB   
977         977  Q30  5D7  A86003  0501060D0AAABAB   
978         978  Q30  5D7  A86003  0501070I0AAABAB   
979         979  Q30  5D7  A86003  0501080D0AAACAC   
980         980  Q30  5D7  A86003  0501080D0AAAHAH   
981         981  Q30  5D7  A86003  0501080D0BGAAAH   
982         982  Q30  5D7  A86003  0501080W0AAADAD   
983         983  Q30  5D7  A86003  0501080W0AAAEAE   
984         984  Q30  5D7  A86003  0501080W0AAAIAI   
985         985  Q30  5D7  A86003  0501100H0AAAFAF   
986         986  Q30  5D7  A86003  0501110C0AAAEAE   
987         987  Q30  5D7  A86003  0501110C0AAAIAI   
988         988  Q30  5D7  A86003  0501110C0AAAJAJ   
989         989  Q30  5D7  A86003  0501110G0AAABAB   
990         990  Q30  5D7  A86003  0501120L0AAAAAA   
991         991  Q30  5D7  A86003  0501120L0AAAFAF   
992         992  Q30  5D7  A86003  0501120L0AAAJAJ   
993         993  Q30  5D7  A86003  0501120P0AAAAAA   
994         994  Q30  5D7  A86003  0501130R0AAAAAA   
995         995  Q30  5D7  A86003  0501130R0AAABAB   
996         996  Q30  5D7  A86003  0501130R0AAADAD   
997         997  Q30  5D7  A86003  0502000G0AAAAAA   
998         998  Q30  5D7  A86003  0502000G0AAABAB   
999         999  Q30  5D7  A86003  0502000M0AAAAAA   

                                            4      5        6        7  \
0    Amoxicillin_Oral Susp 125mg/5ml             1.0     1.69     1.59   
1    Co-Magaldrox_Susp 195mg/220mg/5ml S/F      44.0   124.96   116.45   
2    Maalox_Susp 195mg/220mg/5ml S/F             1.0     5.58     5.17   
3    Mucogel_Susp 195mg/220mg/5ml S/F            1.0     1.71     1.61   
4    Asilone_Susp S/F                            1.0     1.95     1.83   
5    Simeticone_Susp 40mg/ml S/F                 1.0     2.26     2.11   
6    Infacol_Susp 40mg/ml S/F                    1.0     4.52     4.19   
7    Gppe Liq_Gaviscon S/F                       1.0     5.24   

In [5]:
pdp['10']= pdp['10'].str.split(' ', n = 1, expand = True)

In [6]:
pdp.head(n=1000)

Unnamed: 0    0    1       2                3  \
0             0  Q30  5D7  A86001  0501013B0AAAJAJ   
1             1  Q30  5D7  A86003  0101010G0AAABAB   
2             2  Q30  5D7  A86003  0101010G0BBABAB   
3             3  Q30  5D7  A86003  0101010G0BCABAB   
4             4  Q30  5D7  A86003  0101010L0BBABAA   
5             5  Q30  5D7  A86003  0101010R0AAABAB   
6             6  Q30  5D7  A86003  0101010R0BCAAAB   
7             7  Q30  5D7  A86003  0101021B0AAAHAH   
8             8  Q30  5D7  A86003  0101021B0AAAJAJ   
9             9  Q30  5D7  A86003  0101021B0AAAPAP   
10           10  Q30  5D7  A86003  0101021B0AAAQAQ   
11           11  Q30  5D7  A86003  0101021B0BEADAJ   
12           12  Q30  5D7  A86003  0101021B0BEAIAL   
13           13  Q30  5D7  A86003  0101021B0BEAKAQ   
14           14  Q30  5D7  A86003  0101021B0BEAQAP   
15           15  Q30  5D7  A86003  0101021B0BFAAAF   
16           16  Q30  5D7  A86003  0101021B0BIAAAH   
17           17  Q30  5D7  A86003  0102000J0AAABAB   
18           18  Q30  5D7  A86003  0102000J0AAACAC   
19           19  Q30  5D7  A86003  0102000L0AAADAD   
20           20  Q30  5D7  A86003  0102000N0AAABAB   
21           21  Q30  5D7  A86003  0102000N0BBAAAB   
22           22  Q30  5D7  A86003  0102000P0AAABAB   
23           23  Q30  5D7  A86003  0102000P0AAADAD   
24           24  Q30  5D7  A86003  0102000P0BCABAB   
25           25  Q30  5D7  A86003  0102000T0AAAAAA   
26           26  Q30  5D7  A86003  0102000X0AAAAAA   
27           27  Q30  5D7  A86003  0102000Y0AAAFAF   
28           28  Q30  5D7  A86003  0103010D0AAAAAA   
29           29  Q30  5D7  A86003  0103010D0AAABAB   
..          ...  ...  ...     ...              ...   
970         970  Q30  5D7  A86003  0501050A0AAABAB   
971         971  Q30  5D7  A86003  0501050B0AAAAAA   
972         972  Q30  5D7  A86003  0501050B0AAADAD   
973         973  Q30  5D7  A86003  0501050C0AAABAB   
974         974  Q30  5D7  A86003  0501050C0AAAKAK   
975         975  Q30  5D7  A86003  0501050H0AAAAAA   
976         976  Q30  5D7  A86003  0501050H0AAABAB   
977         977  Q30  5D7  A86003  0501060D0AAABAB   
978         978  Q30  5D7  A86003  0501070I0AAABAB   
979         979  Q30  5D7  A86003  0501080D0AAACAC   
980         980  Q30  5D7  A86003  0501080D0AAAHAH   
981         981  Q30  5D7  A86003  0501080D0BGAAAH   
982         982  Q30  5D7  A86003  0501080W0AAADAD   
983         983  Q30  5D7  A86003  0501080W0AAAEAE   
984         984  Q30  5D7  A86003  0501080W0AAAIAI   
985         985  Q30  5D7  A86003  0501100H0AAAFAF   
986         986  Q30  5D7  A86003  0501110C0AAAEAE   
987         987  Q30  5D7  A86003  0501110C0AAAIAI   
988         988  Q30  5D7  A86003  0501110C0AAAJAJ   
989         989  Q30  5D7  A86003  0501110G0AAABAB   
990         990  Q30  5D7  A86003  0501120L0AAAAAA   
991         991  Q30  5D7  A86003  0501120L0AAAFAF   
992         992  Q30  5D7  A86003  0501120L0AAAJAJ   
993         993  Q30  5D7  A86003  0501120P0AAAAAA   
994         994  Q30  5D7  A86003  0501130R0AAAAAA   
995         995  Q30  5D7  A86003  0501130R0AAABAB   
996         996  Q30  5D7  A86003  0501130R0AAADAD   
997         997  Q30  5D7  A86003  0502000G0AAAAAA   
998         998  Q30  5D7  A86003  0502000G0AAABAB   
999         999  Q30  5D7  A86003  0502000M0AAAAAA   

                                            4      5        6        7  \
0    Amoxicillin_Oral Susp 125mg/5ml             1.0     1.69     1.59   
1    Co-Magaldrox_Susp 195mg/220mg/5ml S/F      44.0   124.96   116.45   
2    Maalox_Susp 195mg/220mg/5ml S/F             1.0     5.58     5.17   
3    Mucogel_Susp 195mg/220mg/5ml S/F            1.0     1.71     1.61   
4    Asilone_Susp S/F                            1.0     1.95     1.83   
5    Simeticone_Susp 40mg/ml S/F                 1.0     2.26     2.11   
6    Infacol_Susp 40mg/ml S/F                    1.0     4.52     4.19   
7    Gppe Liq_Gaviscon S/F                       1.0     5.24   

In [7]:
UK_Admin = pd.read_csv('../BL_Work/Admin areas.csv')

In [8]:

UK_postCode = pd.read_csv('../BL_Work/Postcode districts.csv')
UK_postCode.head()
# len(UK_postCode)

Postcode  Latitude  Longitude   Easting  Northing Grid Reference  \
0      AB1   57.1269   -2.13644  391839.0  804005.0       NJ918040   
1      AB2   57.1713   -2.14152  391541.0  808948.0       NJ915089   
2      AB3   57.0876   -2.59624  363963.0  799780.0       NO639997   
3      AB4   57.5343   -2.12713  392487.0  849358.0       NJ924493   
4      AB5   57.4652   -2.64764  361248.0  841843.0       NJ612418   

                         Town/Area    Region  Postcodes  Active postcodes  \
0                         Aberdeen  Aberdeen     2655.0               0.0   
1                         Aberdeen  Aberdeen     3070.0               0.0   
2                         Aberdeen  Aberdeen     2168.0               0.0   
3  Fraserburgh, Peterhead, Macduff  Aberdeen     2956.0               0.0   
4        Buckie, Huntly, Inverurie  Aberdeen     3002.0               0.0   

   Population  Households                                   Nearby districts  
0         NaN         NaN  AB10, AB15, AB9, AB25, AB2, AB12, AB16, AB11, ...  
1         NaN         NaN  AB16, AB22, AB24, AB25, AB1, AB9, AB15, AB10, ...  
2         NaN         NaN  AB31, AB34, AB52, AB33, AB14, AB32, AB30, AB13...  
3         NaN         NaN  AB41, AB43, AB42, AB53, AB22, AB23, AB2, AB24,...  
4         NaN         NaN  AB54, AB52, AB45, AB53, AB33, AB44, AB55, AB51...

In [9]:
UK_postCode.columns

Index([u'Postcode', u'Latitude', u'Longitude', u'Easting', u'Northing',
       u'Grid Reference', u'Town/Area', u'Region', u'Postcodes',
       u'Active postcodes', u'Population', u'Households', u'Nearby districts'],
      dtype='object')

In [10]:
district_pop = {}
for index , row in UK_Admin.iterrows():
    district_pop[row['District']] = row['Population']
    

In [11]:
districts = set(UK_postCode['Region']).intersection(UK_Admin['District'])

In [12]:
districts

{'Aberdeenshire',
 'Adur',
 'Allerdale',
 'Amber Valley',
 'Angus',
 'Argyll and Bute',
 'Arun',
 'Ashfield',
 'Ashford',
 'Aylesbury Vale',
 'Babergh',
 'Barking and Dagenham',
 'Barnet',
 'Barnsley',
 'Barrow-in-Furness',
 'Basildon',
 'Bassetlaw',
 'Bath and North East Somerset',
 'Bedford',
 'Belfast',
 'Bexley',
 'Birmingham',
 'Blackburn with Darwen',
 'Blackpool',
 'Blaenau Gwent',
 'Bolsover',
 'Bolton',
 'Boston',
 'Bracknell Forest',
 'Bradford',
 'Braintree',
 'Breckland',
 'Brent',
 'Brentwood',
 'Bridgend',
 'Brighton and Hove',
 'Bromley',
 'Bromsgrove',
 'Broxbourne',
 'Broxtowe',
 'Burnley',
 'Bury',
 'Caerphilly',
 'Calderdale',
 'Cambridge',
 'Camden',
 'Cannock Chase',
 'Canterbury',
 'Cardiff',
 'Carlisle',
 'Carmarthenshire',
 'Castle Point',
 'Central Bedfordshire',
 'Ceredigion',
 'Charnwood',
 'Chelmsford',
 'Cherwell',
 'Cheshire East',
 'Cheshire West and Chester',
 'Chesterfield',
 'Chichester',
 'Chiltern',
 'Chorley',
 'City of London',
 'Colchester',
 'Con

In [13]:
postCodeDict = {}
for name, group in UK_postCode.groupby('Region'):
    if name in districts:
        postCodeDict[name] = {}
        postCodeDict[name]['postcodes']=list(group['Nearby districts'])
        postCodeDict[name]['pop'] = district_pop[name]

for k in postCodeDict:
    actualcodes = []
    codes = postCodeDict[k]['postcodes']
    for c in codes:
        try:
            actualcodes+= [w.strip() for w in c.split(',')]
        except:
            print c
    postCodeDict[k]['postcodes'] = actualcodes
print postCodeDict

nan
nan
nan
nan
nan
nan
nan
{'Rhondda Cynon Taf': {'postcodes': ['CF38', 'CF39', 'CF46', 'CF45', 'CF8', 'CF83', 'CF15', 'CF72', 'CF40', 'CF82', 'CF37', 'CF15', 'CF72', 'CF39', 'CF46', 'CF83', 'CF45', 'CF7', 'CF4', 'CF8', 'CF40', 'CF43', 'CF37', 'CF72', 'CF41', 'CF7', 'CF45', 'CF38', 'CF44', 'CF42', 'CF43', 'CF39', 'CF41', 'CF44', 'CF42', 'CF37', 'CF45', 'CF72', 'CF7', 'CF35', 'CF43', 'CF40', 'CF42', 'CF44', 'CF39', 'CF45', 'CF35', 'CF32', 'CF37', 'CF46', 'CF41', 'CF43', 'CF40', 'CF44', 'CF35', 'CF39', 'CF45', 'CF32', 'CF34', 'CF31', 'CF40', 'CF41', 'CF44', 'CF39', 'CF42', 'CF45', 'CF46', 'CF48', 'CF47', 'CF37', 'CF43', 'CF41', 'CF40', 'CF48', 'CF47', 'CF42', 'CF45', 'CF39', 'CF46', 'NP24', 'CF46', 'CF48', 'CF47', 'CF37', 'CF43', 'CF39', 'CF38', 'CF40', 'CF44', 'CF41', 'CF7', 'CF38', 'CF39', 'CF15', 'CF35', 'CF37', 'CF71', 'CF40', 'CF43', 'CF45'], 'pop': 234387}, 'Mendip': {'postcodes': ['BA7', 'BA10', 'BS39', 'BA5', 'BA3', 'BA6', 'BA9', 'BS18', 'DT9', 'BA16', 'BA6', 'BA4', 'BA16', 'BS4

In [14]:
# postCodeDict

In [15]:
diseaseMatched = json.load(open('DiseasesMatched.json','rb'))

In [16]:
symMatched = json.load(open('SymptomsMatched.json','rb'))

In [17]:
symMatched

{u'"Abdominal+bloating"': {u'MatchedDrugs': [[u'Magaldrate']],
  u'Synonyms': [u'Matched Synonyms:  Abdominal bloating  ']},
 u'"Abdominal+pain"': {u'MatchedDrugs': [[u'Hyoscyamine']],
  u'Synonyms': [u'Matched Synonyms:  Abdominal Pain ... Abdominal pain NOS  ']},
 u'"Abnormal+gait"': {u'MatchedDrugs': [], u'Synonyms': []},
 u'"Abnormal+sexual+function"': {u'MatchedDrugs': [], u'Synonyms': []},
 u'"Amnesia"': {u'MatchedDrugs': [], u'Synonyms': []},
 u'"Anger+reaction"': {u'MatchedDrugs': [], u'Synonyms': []},
 u'"Anxiety"': {u'MatchedDrugs': [[u'Bromazepam ',
    u' Chlordiazepoxide ',
    u' Clorazepic acid ',
    u' Hydroxyzine'],
   [u'Buspirone ',
    u' Chlordiazepoxide ',
    u' Diazepam ',
    u' Lorazepam ',
    u' Meprobamate ',
    u' Oxazepam'],
   [u'Chlorpromazine'],
   [u'Acetylsalicylic acid ',
    u' Alprazolam ',
    u' Amoxapine ',
    u' Chlordiazepoxide ',
    u' Diazepam ',
    u' Doxepin ',
    u' Lorazepam ',
    u' Maprotiline ',
    u' Methotrimeprazine ',
   

In [18]:
# diseaseMatched

In [19]:
def countDiseasePrescriptions(boroughDict,diseasedPriscriptions):
    diseasePrescriptionCount = {}
    for k in boroughDict:
        if k not in diseasePrescriptionCount:
            diseasePrescriptionCount[k] = 0
            areas = boroughDict[k]['postcodes']
            area_disease = diseasedPriscriptions[diseasedPriscriptions['10'].isin(areas)]
            diseasePrescriptionCount[k] = len(area_disease)
    return diseasePrescriptionCount


def countAllPrescriptions(boroughDict,allPriscriptions):
    allPrescriptionCount = {}
    for k in boroughDict:
        if k not in allPrescriptionCount:
            allPrescriptionCount[k] = 0
            areas = boroughDict[k]['postcodes']
            all_disease = allPriscriptions[allPriscriptions['10'].isin(areas)]
            allPrescriptionCount[k] = len(all_disease)
    return allPrescriptionCount
        

In [20]:
# monthDisease = {}
# for f in files:
#     month = f.split('/')[-1].split('.')[0]
#     logger.debug("Working with %s month",month)
#     pdp = pd.read_csv(f,compression='gzip')
#     pdp['10']= pdp['10'].str.split(' ', n = 1, expand = True)
#     monthDisease[month]={}
#     for d in diseaseMatched:
#         key = d.replace('\"','').replace('+',' ').replace('\\','')
#         disease_df = pdp[pdp['12'] == key]
#         logger.debug("Working with disease %s with total %d prescriptions",(key,len(disease_df)))
#         disease_prescriptions = countDiseasePrescriptions(postCodeDict,disease_df)
#         monthDisease[month][d] = disease_prescriptions
        

In [21]:
# monthDisease

In [22]:
# %store monthDisease

In [24]:
monthSymptom = {}
for f in files:
    month = f.split('/')[-1].split('.')[0]
    logger.debug("Working with %s month",month)
    pdp = pd.read_csv(f,compression='gzip')
    pdp['10']= pdp['10'].str.split(' ', n = 1, expand = True)
    monthSymptom[month]={}
    for d in tqdm(symMatched):
        key = d.replace('\"','').replace('+',' ').replace('\\','')
        disease_df = pdp[pdp['13'] == key]
        logger.debug("Working with disease %s with total %d prescriptions",key,len(disease_df))
        disease_prescriptions = countDiseasePrescriptions(postCodeDict,disease_df)
        monthSymptom[month][d] = disease_prescriptions

100%|██████████| 115/115 [02:22<00:00,  1.24s/it]


In [26]:
monthSymptom

{'201008': {u'"Abdominal+bloating"': {'Aberdeenshire': 0,
   'Adur': 0,
   'Allerdale': 0,
   'Amber Valley': 0,
   'Angus': 0,
   'Argyll and Bute': 0,
   'Arun': 0,
   'Ashfield': 0,
   'Ashford': 0,
   'Aylesbury Vale': 0,
   'Babergh': 0,
   'Barking and Dagenham': 0,
   'Barnet': 0,
   'Barnsley': 0,
   'Barrow-in-Furness': 0,
   'Basildon': 0,
   'Bassetlaw': 0,
   'Bath and North East Somerset': 0,
   'Bedford': 0,
   'Belfast': 0,
   'Bexley': 0,
   'Birmingham': 0,
   'Blackburn with Darwen': 0,
   'Blackpool': 0,
   'Blaenau Gwent': 0,
   'Bolsover': 0,
   'Bolton': 0,
   'Boston': 0,
   'Bracknell Forest': 0,
   'Bradford': 0,
   'Braintree': 0,
   'Breckland': 0,
   'Brent': 0,
   'Brentwood': 0,
   'Bridgend': 0,
   'Brighton and Hove': 0,
   'Bromley': 0,
   'Bromsgrove': 0,
   'Broxbourne': 0,
   'Broxtowe': 0,
   'Burnley': 0,
   'Bury': 0,
   'Caerphilly': 0,
   'Calderdale': 0,
   'Cambridge': 0,
   'Camden': 0,
   'Cannock Chase': 0,
   'Canterbury': 0,
   'Cardiff':

In [28]:
%store monthSymptom

Stored 'monthSymptom' (dict)
